<a href="https://colab.research.google.com/github/serivan/DeepLearning/blob/master/Keras/bertviz_example.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


Installazione delle librerie Transformers (https://huggingface.co/transformers/index.html) e BertViz (https://github.com/jessevig/bertviz)



In [ ]:
!pip install regex
!pip install transformers
!pip install boto3

import sys
!test -d bertviz_repo && echo "FYI: bertviz_repo directory already exists, to pull latest version uncomment this line: !rm -r bertviz_repo"
# !rm -r bertviz_repo # Uncomment if you need a clean pull from repo
!test -d bertviz_repo || git clone https://github.com/jessevig/bertviz bertviz_repo
if not 'bertviz_repo' in sys.path:
  sys.path += ['bertviz_repo']


FYI: bertviz_repo directory already exists, to pull latest version uncomment this line: !rm -r bertviz_repo


Import delle funzioni di Transformers e di BertViz

In [ ]:
from transformers import AutoTokenizer, AutoModel
from bertviz_repo.bertviz import head_view, model_view

Codice per la visualizzazione (si adatta meglio al Colab, poco importante)

In [ ]:
def show_model_view(model, tokenizer, sentence_a, sentence_b=None, hide_delimiter_attn=False):
    inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    if sentence_b:
        token_type_ids = inputs['token_type_ids']
        attention = model(input_ids, token_type_ids=token_type_ids)[-1]
        sentence_b_start = token_type_ids[0].tolist().index(1)
    else:
        attention = model(input_ids)[-1]
        sentence_b_start = None
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)
    if hide_delimiter_attn:
        for i, t in enumerate(tokens):
            if t in ("[SEP]", "[CLS]"):
                for layer_attn in attention:
                    layer_attn[0, :, i, :] = 0
                    layer_attn[0, :, :, i] = 0
    model_view(attention, tokens, sentence_b_start)

def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/5.7.0/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

Carico il modello "base-uncased" pre-allenato dalla libreria Transformers


output_attentions mostra anche i pesi di tutte le head (necessari per la visualizzazione)

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased", do_lower_case=True)
model = AutoModel.from_pretrained("bert-base-uncased", output_attentions=True)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Uso una frase di esempio

*The safety and efficacy of anakinra used in combination with HUMIRA has not been studied.*

Faccio per prima cosa la tokenizzazione

In [ ]:
sentence_a = "The safety and efficacy of anakinra used in combination with HUMIRA has not been studied."
inputs = tokenizer.encode_plus(sentence_a, return_tensors='pt', add_special_tokens=True)
token_type_ids = inputs['token_type_ids']
input_ids = inputs['input_ids']
input_id_list = input_ids[0].tolist()
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
print(tokens)

['[CLS]', 'the', 'safety', 'and', 'efficacy', 'of', 'ana', '##kin', '##ra', 'used', 'in', 'combination', 'with', 'hum', '##ira', 'has', 'not', 'been', 'studied', '.', '[SEP]']


Eseguo BERT ed estraggo i pesi di tutte le head

In [ ]:
bert_results = model(input_ids, token_type_ids=token_type_ids)
attention_heads = bert_results[-1]
print("Numero di livelli di encoder:", len(attention_heads))
print("Risultato per ogni livello:", list(attention_heads[0].shape))

Numero di livelli di encoder: 12
Risultato per ogni livello: [1, 12, 21, 21]


Visualizzazione di tutte le head:

In [ ]:
call_html()
model_view(attention_heads, tokens)

<IPython.core.display.Javascript object>

Visualizzazione per livello:

In [ ]:
head_view(attention_heads, tokens)

<IPython.core.display.Javascript object>